In [ ]:
# !pip install torchtext==0.6
# from google.colab import drive
# drive.mount('/content/drive')

# with open('/content/drive/My Drive/Assignment4_2/trainen.txt', encoding='utf8') as f:
#     eng_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
# with open('/content/drive/My Drive/Assignment4_2/trainta.txt', encoding='utf8') as f:
#     tamil_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
# with open('/content/drive/My Drive/Assignment4_2/deven.txt', encoding='utf8') as f:
#     eng_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
# with open('/content/drive/My Drive/Assignment4_2/devta.txt', encoding='utf8') as f:
#     tamil_test = list(map(lambda x: x.rstrip(), f.readlines()))

# embedding_glove = pickle.load(open('/content/drive/My Drive/Assignment4_2/glove.sav', 'rb'))


In [1]:
import pdb
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'

In [2]:
import torch
import torch.nn as nn
from torch.nn import TransformerEncoder, TransformerEncoderLayer, TransformerDecoder, TransformerDecoderLayer, Transformer
import torch.nn.functional as F
import numpy as np
import torch.optim as optim
from torchtext.vocab import GloVe
from torchtext.data import Field, BucketIterator
from torchtext.data.metrics import bleu_score
import spacy
import math

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cuda')

In [4]:
#Reading files

with open('trainen.txt', encoding='utf8') as f:
    eng_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('trainta.txt', encoding='utf8') as f:
    tamil_train = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('deven.txt', encoding='utf8') as f:
    eng_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
with open('devta.txt', encoding='utf8') as f:
    tamil_test = list(map(lambda x: x.rstrip(), f.readlines()))
    
embedding_glove = GloVe(name='6B', dim=100)

spacy_en = spacy.load('en_core_web_sm')

def tokenize_en(text):
    return [tok.text for tok in spacy_en.tokenizer(text)]

stop_words = [',','.','?','!',')','(',':',']','[','$','#','&','%','--']
ENG = Field(tokenize = tokenize_en, init_token='sos', eos_token = 'eos', lower=True, stop_words=stop_words)
processed_eng_train = list(map(lambda x: ENG.preprocess(x), eng_train))
processed_eng_test = list(map(lambda x: ENG.preprocess(x), eng_test))

ENG.build_vocab(processed_eng_train, vectors=embedding_glove)

In [5]:
def preprocess(processed_eng):
    
    #function to return the numericalized version of the tokenized sentences
    X = []
    for tokenized_sentence in processed_eng:
        int_sequence = [2]  #first element is the SOS token 
        for token in tokenized_sentence:
            int_sequence.append(ENG.vocab.stoi[token])
        int_sequence.append(3) #last element is the EOS token
        X.append(int_sequence)
    
    return X

# X_train and X_test are lists of lists with the integer sequences for a given sentence
X_train = preprocess(processed_eng_train)
X_test = preprocess(processed_eng_test)

In [6]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

# Same thing for Tamil sentences
TAM = Tokenizer()
TAM.fit_on_texts(tamil_train)
Y_train = TAM.texts_to_sequences(tamil_train)
Y_test = TAM.texts_to_sequences(tamil_test)

#adding EOS token
EOS = len(TAM.word_index)+2
SOS = len(TAM.word_index)+1
_ = [y.append(EOS) for y in Y_train]
_ = [y.append(EOS) for y in Y_test]
_ = [y.insert(0,SOS) for y in Y_train]
_ = [y.insert(0,SOS) for y in Y_test]

Y_train = pad_sequences(Y_train, padding='post', value=0, maxlen=30)
Y_test = pad_sequences(Y_test, padding='post', value=0, maxlen=30)

Using TensorFlow backend.


In [7]:
TAM.index_word[0] = 'PAD'
TAM.index_word[len(TAM.index_word)] = 'SOS'
TAM.index_word[len(TAM.index_word)] = 'EOS'

In [8]:
Y_train[0]

array([18669,    11,    63,   359,     7, 18670,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0])

In [9]:
# pre-padding the inputs with value 1, from the dictionary ENG.vocab.stoi
X_train = pad_sequences(X_train, padding='pre', value=1, maxlen=55)
X_test = pad_sequences(X_test, padding='pre', value=1, maxlen=55)

In [10]:
len(Y_test[0])

30

In [11]:
source_vocab_size = len(ENG.vocab)
target_vocab_size = len(TAM.index_word)
print(source_vocab_size)
print(target_vocab_size)

9723
18671


In [14]:
# Code to load a model and save embeddings as a numpy array for later use
# import fasttext.util
# ft = fasttext.load_model('cc.ta.300.bin')
# fasttext.util.reduce_model(ft, 100)
# tamil_embedding = torch.zeros(target_vocab_size, 100)
# for i in range(target_vocab_size):
#     tamil_embedding[i] = torch.FloatTensor(ft.get_word_vector(TAM.index_word[i]))

# X = tamil_embedding.numpy()
# np.save('tam_embed_q5.npy', X)

In [15]:
# loading pretrained weights from numpy file
tamil_embedding = np.load('tam_embed_q5.npy')
tamil_embedding = torch.from_numpy(tamil_embedding)

In [16]:
from torch.utils.data import Dataset, DataLoader, ConcatDataset, random_split

class DatasetClass(Dataset):
    
    def __init__(self, source, target):
        
        self.source = source
        self.target = target
      
    def __len__(self):
        
        return len(self.source)
    
    def __getitem__(self, idx):
        
        return self.source[idx], self.target[idx]

In [17]:
def train_test_loader(source_train, target_train, source_test, target_test, num_workers=0, batch_size=32):

    train_data = DatasetClass(source_train, target_train)
    test_data = DatasetClass(source_test, target_test)

    trainloader = DataLoader(train_data, batch_size=batch_size, shuffle=True, num_workers=num_workers)
    testloader = DataLoader(test_data, batch_size=batch_size, shuffle=True, num_workers=num_workers)
    
    return trainloader, testloader

In [45]:
class PositionEncoding(nn.Module):

    def __init__(self, dim, max_length=55):
        
        super(PositionEncoding, self).__init__()
        pos_enc = torch.zeros(max_length, dim)
        index = torch.arange(0, max_length, dtype=torch.float).unsqueeze(1)
        # The denominator terms (10000)^(2j/d)
        denominator = torch.exp(torch.arange(0, dim, 2).float() * (-math.log(10000.0) / dim))
        # even columns use sin
        pos_enc[:, 0::2] = torch.sin(index * denominator)
        # odd columns use cos
        pos_enc[:, 1::2] = torch.cos(index * denominator)
        pos_enc = pos_enc.unsqueeze(0).transpose(0, 1)    # 55 x 1 x 100
        print('pos_enc.shape', pos_enc.shape)
        
        # to prevent the optimiser from changing the position encodings
        self.register_buffer('pos_enc', pos_enc)

    def forward(self, x):
        x = x + self.pos_enc[:x.size(0), :]
        return x

In [46]:
class Transformer(nn.Module):
    
    def __init__(self, target_vocab_size, embed_size, num_heads, num_layers, dropout, ENG, tamil_embedding):
        
        super(Transformer, self).__init__()
        self.pos_encoder = PositionEncoding(embed_size)
        self.encoder = nn.Embedding.from_pretrained(ENG.vocab.vectors)
        self.transformer = nn.Transformer(embed_size, num_heads, num_layers, num_layers, dropout=dropout)
        self.decoder = nn.Embedding.from_pretrained(tamil_embedding)
        self.fc = nn.Linear(embed_size, target_vocab_size)
        self.logsoftmax = nn.LogSoftmax(dim=2)
        
    def forward(self, src, trg):
        
        # src and trg will be of sizes: batch_size x Ts and batch_size x Tt
        src_pad_mask = (src==1).to(device) # 1 is the padding used for source
        trg_pad_mask = (trg==0).to(device) # 0 is the padding used for target
        src = self.encoder(src)     # batch_size x Ts x 100
        src = self.pos_encoder(src.transpose(0,1)) # Ts x batch_size x 100
        trg = self.decoder(trg)     # batch_size x Tt x 100
        trg = self.pos_encoder(trg.transpose(0,1)) # Tt x batch_size x 100
        #src_mask = (torch.tril(torch.ones(src.shape[0], src.shape[0])) == 0).to(device)
        trg_mask = (torch.tril(torch.ones(trg.shape[0], trg.shape[0])) == 0).to(device)
        output = self.transformer(src, trg, tgt_mask=trg_mask, src_key_padding_mask=src_pad_mask, tgt_key_padding_mask=trg_pad_mask) 
        output = self.fc(output)  # output will now be Tt x batch_size x target_vocab_size
        output = self.logsoftmax(output)
        
        return output

In [47]:
embed_size = 100
num_heads = 4
num_layers = 2
dropout = 0.1
trans_model = Transformer(target_vocab_size, embed_size, num_heads, num_layers, dropout, ENG, tamil_embedding)

pos_enc.shape torch.Size([55, 1, 100])


In [48]:
trans_model = trans_model.to(device)

In [49]:
def train_model(trainloader, trans):
    
    loss_fn = nn.NLLLoss()
    trans_optimiser = optim.Adam(trans.parameters())
    
    max_epochs = 100
    old_loss = np.inf
    
    for epoch in range(max_epochs):
        
        running_loss = 0.0
    
        for i in trainloader:
            
            loss_val = 0
            i[0] = i[0].type(torch.LongTensor)   # batch_size x Ts
            i[1] = i[1].type(torch.LongTensor)   # batch_size x Tt
            source_batch = i[0].to(device)
            target_batch = i[1].to(device)

            output = trans(source_batch, target_batch)  # Tt x batch_size x target_vocab_size

            # calculating loss for the batch
            for j in range(output.shape[1]):
                logprobs = output[:, j, :].squeeze(1)
                target_classes = target_batch[j].squeeze(0)
                # inputs to NLL Loss should be of sizes Tt x n_classes and Tt
                loss_val += loss_fn(logprobs, target_classes)

            loss_val.backward()
            
            nn.utils.clip_grad_norm_(trans.parameters(), 0.5)

            trans_optimiser.step()
            
            running_loss += loss_val.item()
        
        print('Epoch', epoch+1, ': Loss =', running_loss)
        
        if abs(running_loss-old_loss)/running_loss < 1e-3:
            print('Converged')
            break
            
        old_loss = running_loss
    
    print('Finished Training')

In [51]:
trainloader, _ = train_test_loader(X_train, Y_train, X_test, Y_test)

In [34]:
#torch.save(trans_model.state_dict(), 'q5_wts.pt')

In [55]:
trans_model.load_state_dict(torch.load('q5_wts.pt'))

<All keys matched successfully>

In [52]:
train_model(trainloader, trans_model)

Epoch 1 : Loss = 26954.266848564148
Epoch 2 : Loss = 14730.003588199615
Epoch 3 : Loss = 9473.605902671814
Epoch 4 : Loss = 6307.763416171074
Epoch 5 : Loss = 4282.915403962135
Epoch 6 : Loss = 2931.306756079197
Epoch 7 : Loss = 1999.673041343689
Epoch 8 : Loss = 1413.0455384254456
Epoch 9 : Loss = 1077.5161756575108
Epoch 10 : Loss = 874.5115242004395


KeyboardInterrupt: 

In [53]:
# For testing, we load the data with batchsize=1
_ , testloader = train_test_loader(X_train, Y_train, X_test, Y_test, batch_size=1)

In [30]:
# trainloader with batch_size = 1 must be used for testing
from nltk.translate.bleu_score import sentence_bleu, corpus_bleu

def test_model(testloader, trans_model):
    
    all_target = []
    all_predicted = []
    
    with torch.no_grad():
    
        for i in testloader:

            i[0] = i[0].type(torch.LongTensor)   # batch_size x Ts
            i[1] = i[1].type(torch.LongTensor)   # batch_size x Tt
            source_sentence = i[0].to(device)
            target_sentence = i[1].to(device)
            y_t = torch.cuda.LongTensor([SOS]).unsqueeze(0)  # 1 x 1
            Tt = i[1].shape[1]  # 30
            for i in range(Tt):
                # y_t is appended to make it of size 1 x t at every time
                output = trans_model(source_sentence, y_t)
                last_output = output[-1,:,:]
                last_output = last_output.squeeze(0) # to make it 1 x target_vocab_size
                _ , index = last_output.topk(1)
                latest_predicted = index
                if latest_predicted == EOS:
                    #print('eos')
                    break
                else:
                    y_t = torch.cat((y_t, latest_predicted.unsqueeze(0)), dim=1)
                    
            predicted = []
            target = []
            
            for i in y_t.squeeze():
                if i.item() not in [SOS, 0]:
                    predicted.append(TAM.index_word[i.item()])
            
            for i in target_sentence.squeeze():
                if i.item()==0:
                    break
                elif i.item() not in [EOS,SOS]:
                    target.append(TAM.index_word[i.item()])
                    
            target = [target]
            print("Predicted:",predicted)
            print("Target:",target)
            # print("Predicted tokens=", y_t)
            # print('Target=', target_sentence)
            
            all_target.append(target)
            all_predicted.append(predicted)
            
            
        bleu1 = corpus_bleu(all_target, all_predicted, weights=(1.0, 0, 0, 0))
        bleu2 = corpus_bleu(all_target, all_predicted, weights=(0.5, 0.5, 0, 0))
        bleu3 = corpus_bleu(all_target, all_predicted, weights=(1/3, 1/3, 1/3, 0))
        bleu4 = corpus_bleu(all_target, all_predicted)
                

    
    return bleu1, bleu2, bleu3, bleu4

In [56]:
test_model(testloader, trans_model)

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'நீங்கள்கொண்டுவருகின்றன', 'சேர்ந்துக்கலாமா', 'சேர்ந்துக்கலாமா', 'சேர்ந்துக்கலாமா', 'நீங்கள்என்னைபார்க்கதெரியவில்லை', '♪ஓ', 'பொருத்தப்பட்டிருந்தன', 'பொருத்தப்பட்டிருந்தன', 'மற்றும்', 'மற்றும்', 'மற்றும்', 'மற்றும்', 'மற்றும்', 'உணர்வீர்கள்', 'உன்னோடு', 'உன்னோடு', 'முடியாது', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நாங்கள்', 'எங்கள்', 'ஆடியோ', 'மன்னிப்பு', 'ஆனால்', 'வழியில்', 'விஷயங்கள்', 'இங்கே', 'இன்று', 'வெளியே', 'தெரிகிறது']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'பேரக்குழந்தைகள்', 'தனமான', 'தனமான', 'தனமான', 'தனமான', 'தனமான', 'தனமான', 'தனமான', 'தனமான', 'செய்து', 'விட்டு', 'விட்டு', 'விட்டு', 'சாரி', 'நீங்கள்', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['உனக்கு', 'தெரியாது', 'இது', 'வேற', 'பத்திரிக்கை', 'இதுல', 'புகைப்படத்தை']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'இதுஜாக்', 'தொழிலாளர்கள', 'தொழி

Predicted: ['கார்டியன்', 'கார்டியன்', 'கார்டியன்', 'கேட்டுப்பெறக்கூடாது', 'நீங்கள்கொண்டுவருகின்றன', 'நீங்கள்கொண்டுவருகின்றன', 'சிரமத்திற்காக', 'சிரமத்திற்காக', 'சிரமத்திற்காக', 'விஷயங்கள்', 'விஷயங்கள்', 'விஷயங்கள்', 'விஷயங்கள்', 'படங்கள்', 'படங்கள்', 'படங்கள்', 'படங்கள்', 'முடியாது', 'உன்னோடு', 'உன்னோடு', 'வேண்டும்', 'கூற', 'கூற', 'கூற']
Target: [['எனவே', 'நீங்கள்', 'பார்க்க', 'முடியும்', 'என்றால்', 'வேறு', 'வழி', 'இந்த', 'தொல்லை', 'சமாளிக்க', 'நான்', 'கேட்க', 'விரும்புகிறேன்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'அன்பிளாஸ்டிசைடு', 'அன்பிளாஸ்டிசைடு', 'அன்பிளாஸ்டிசைடு', 'நகல்49', 'நகல்49', 'மாதிரி', 'மாதிரி', 'எப்படி', 'எப்படி', 'எப்படி', 'எப்படி', 'எப்படி', 'எப்படி', 'எப்படி', 'ஒரு', 'ஒரு', 'ஒரு', 'ஒரு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நான்', 'கண்ணாடியை', 'சரி', 'நான்', 'ஆய்வு', 'செய்தேன்', 'அவர்கள்', 'முழு', 'இருக்க', 'விரும்புகிறேன்', 'போன்ற', 'அவர்கள்', 'பார்த்து', 'சரியா']]
Predicted: ['வார்த்தை', 'வார்த்தை', 'வார்த்தை', 'வார்த்தை', 'வார்த்தை', 

Predicted: ['அவர்வானத்தில்உயர்மற்றும்கையொப்பம்உள்ளது♪', 'வாடிக்கையாளர்களுடன்', 'வாடிக்கையாளர்களுடன்', 'வாடிக்கையாளர்களுடன்', 'நீங்கள்கொண்டுவருகின்றன', 'நீங்கள்கொண்டுவருகின்றன', 'நீங்கள்கொண்டுவருகின்றன', 'ஒருவேளைஎப்படிஇந்தஅனைத்துபடைப்புகள்சிறந்த', 'ஒருவேளைஎப்படிஇந்தஅனைத்துபடைப்புகள்சிறந்த', 'எதிர்பாக்கறேன்', 'எதிர்பாக்கறேன்', 'தொடுவாங்க', 'தொடுவாங்க', 'தொடுவாங்க', 'தொடுவாங்க', 'படங்கள்', 'படங்கள்', 'விவகாரங்களை', 'கிழக்கு', 'உன்னோடு', 'தவிர', 'ஏன்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'கண்டுபிடிக்க']
Target: [['என்', 'மீட்பவர்', 'தான்', 'எழுப்பிய', 'கேள்விகள்', 'இருப்புஅச்சுறுத்தலானஇருக்கிறது', 'சிந்திக்க', 'வேண்டும்', 'ஆனால்நான்நான்கண்டேன்']]
Predicted: ['கிருஸ்துமஸ்', 'கிருஸ்துமஸ்', 'கிருஸ்துமஸ்', 'கிருஸ்துமஸ்', 'மக்கள்ஒருசிப்பாய்', 'சேர்ந்துக்கலாமா', 'சேர்ந்துக்கலாமா', 'சேர்ந்துக்கலாமா', 'ருமேனியர்கள்', 'ருமேனியர்கள்', 'எல்லோரும்', 'வெளியில்', 'வெளியில்', 'வெளியில்', 'பிறகு', 'பிறகு', 'பிறகு', 'பிறகு', 'பின்னர்', 'உன்னோடு', 'உன்னோடு', 'தவிர', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை

Predicted: ['கூறுகிறோம்', 'கூறுகிறோம்', 'கூறுகிறோம்', 'கூறுகிறோம்', 'கூறினீர்கள்', 'கூறினீர்கள்', 'கூறினீர்கள்', 'கூறினீர்கள்', 'பார்த்திருந்தால்', 'டென்னஸி', 'டென்னஸி', 'டென்னஸி', 'டென்னஸி', 'பெறாமல்', 'பெறாமல்', 'பெறாமல்', 'முடியாது', 'காவலில்', 'காவலில்', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'கண்டுபிடிக்க']
Target: [['இது', 'அல்பேனியர்கள்', 'ஒன்றாகும்', 'நபர்', 'நான்', 'அதை', 'சொல்ல', 'அவரை', 'வேண்டும்', 'நான்', 'சொல்ல', 'அவருக்கு', 'தேவையான', 'ஒன்று', 'என்று']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'ஆசிர்வதிக்க', 'ஆசிர்வதிக்க', 'பயமுறுத்தினா்', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'சொல்லிர்கார்', 'நேரத்தில்', 'நேரத்தில்', 'உணர்வீர்கள்', 'உணர்வீர்கள்', 'உன்னோடு', 'உன்னோடு', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['ஒரு', 'முழு', 'துண்டு', 'நான்', 'வேண்டும்', 'அனைத்து', 'மற்றும்', 'நான்', 'நல்ல', 'இரண்டு', 'நாட்கள்', 'த

Predicted: ['என்சிடபுள்யு', 'தேர்ந்தெடுபாய்', 'தேர்ந்தெடுபாய்', 'தேர்ந்தெடுபாய்', 'தேர்ந்தெடுபாய்', 'சிரமத்திற்காக', 'சிரமத்திற்காக', 'கவனக்குறைவால்', 'கவனக்குறைவால்', 'தாக்குதல்கள்', 'தாக்குதல்கள்', 'தாக்குதல்கள்', 'செயல்கள்', 'செய்தால்', 'செய்தால்', 'செய்தால்', 'முடியுமா', 'முடியுமா', 'உன்னோடு', 'உன்னோடு', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நான்', 'முயற்சி', 'தயாராக', 'இருந்தன', 'கூட', 'நீங்கள்', 'அவர்கள்', 'சொல்வதை', 'நான்', 'என்ன', 'செய்கிறது']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'சந்தோஷ்ம்', 'தோற்றுவிட்டோம்', 'பார்க்கமுடியாத', 'பார்க்கமுடியாத', 'பார்க்கமுடியாத', 'பார்த்திருக்க', 'பார்க்கமுடியாத']
Target: [['மற்றும்', 'காதலர்', 'அட்டை', 'நீங்கள்', 'அபிமன்யு', 'அனுப்பி', 'எல்லோரும்', 'அலுவலகத்தில்', 'அது', 'பிடித்திருந்தது']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'buffet', 'நீதிமன்றத்தில்', 'நீதிமன்றத்தில்', 'உள்ளாடைகளை', 'உள்ளாடைகளை', 'உள்ளாடைகளை', 'லதா', 'லதா', 'லதா', 'லதா', 'இதர', 'இதர', 'இதர', 'ம

...

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'நீங்கள்கொண்டுவருகின்றன', 'சேர்ந்துக்கலாமா', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'முடியும்', 'முடியும்', 'முடியாது', 'முடியாது', 'முடியாது', 'உன்னோடு', 'உன்னோடு', 'நேரத்தில்', 'இல்லை', 'இல்லை', 'கண்டுபிடிக்க']
Target: [['நான்', 'ஆராய்ந்த', 'உன்னை', 'அழைத்து', 'செல்கிறேன்', 'ஆனால்', 'இப்போதுள்ள', 'நிலையில்', 'நாம்', 'அங்கு', 'செல்வது', 'இருக்காது']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'நீங்கள்கொண்டுவருகின்றன', 'சிரமத்திற்காக', 'காரணங்களால்', 'துறையில்', 'துறையில்', 'துறையில்', 'துறையில்', 'முன்பே', 'பிறகு', 'பிறகு', 'பிறகு', 'முடியாது', 'முடியாது', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'கண்டுபிடிக்க']
Target: [['நான்', 'இப்போது', 'அழைப்பு', 'எடுக்க', 'கிடைக்க', 'வில்லை', 'நீங்கள்', 'ஒரு', 'செய்தியை', 'விட்டு', 'ஆனால்']]
Predicted: ['நம்முடையது', 'நம்முடையது', 'நம்முடையது', 

Predicted: ['அவர்வானத்தில்உயர்மற்றும்கையொப்பம்உள்ளது♪', 'நாம்எப்போதும்இந்தபயணம்ஞாபகம்', 'நாம்எப்போதும்இந்தபயணம்ஞாபகம்', 'முட்டாளாக்கினாள்', 'முட்டாளாக்கினாள்', 'பொரிக்கிகளால்', 'பொரிக்கிகளால்', "'எப்படி", 'மாதிரி', 'மாதிரி', 'மாதிரி', 'மாதிரி', 'தகுதி', 'தகுதி', 'தகுதி', 'தகுதி', 'பிடிக்காது', 'உன்னோடு', 'உன்னோடு', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'அவன்', 'இல்லை']
Target: [['இத', 'நான்', 'ரொம்ப', 'தூரத்துல', 'இருந்து', 'உங்களுக்காக', 'கொண்டு', 'வர்றேன்', 'ஆனா', 'இது', 'தான்', 'கடைசி', 'தடவ']]
Predicted: ['கொடுக்கும்', 'கொடுக்கும்', 'கொடுக்கும்', 'கொடுக்கும்', 'கொடுக்கும்', "அவர்களுடன்'", "அவர்களுடன்'", 'offa', 'offa']
Target: [['நாம்', 'அந்த', 'அடையும்', 'வரை', 'நான்', 'யாருக்கும்', 'நன்றி', 'rom']]
Predicted: ['அவர்வானத்தில்உயர்மற்றும்கையொப்பம்உள்ளது♪', 'எடுத்துக்காட்டாக', 'எடுத்துக்கொண்டு', 'எடுத்துக்கொண்டு', 'எடுத்துக்கொண்டு', 'எடுத்துக்கொண்டு', 'வகையெல்லாம்', 'ஒருவேளைஎப்படிஇந்தஅனைத்துபடைப்புகள்சிறந்த', 'ஒருவேளைஎப்படிஇந்தஅனைத்துபடைப்புகள்சிறந்த', '

Predicted: ['ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'ஈவ்', 'புருசன்', 'புருசன்', 'போய்விட்டாள்', 'முயற்சித்து', 'முயற்சித்து', 'இன்னும்', 'இன்னும்', 'கதைகள்', 'இணக்கமான', 'உணர்வீர்கள்', 'உன்னோடு', 'நீங்கள்', 'பற்றி', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['உங்களுக்கு', 'தெரியும்', 'நான்', 'உங்கள்', 'உயிரை', 'காப்பாற்ற', 'நான்', 'உங்கள்', 'சரி', 'கிடைக்கும்']]
Predicted: ['கொடுக்கும்', 'கொடுத்த', 'கொடுத்த', 'கொடுத்த', 'கொடுத்த', 'கொடுத்த', 'கொடுத்தார்', 'கொடுத்தார்', 'பயன்படுத்துகிறது', 'தொடுவாங்க', 'தொடுவாங்க', 'தொடுவாங்க', 'தொடுவாங்க', 'தொடுவாங்க', 'செய்தால்', 'செய்தால்', 'செய்தால்', 'நாம்', 'நாம்', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['இது', 'எனக்கு', 'ஒரு', 'புணர்கிறேன்', 'விளையாட்டு', 'அல்ல', 'எனக்கு', 'என்', 'fucking', 'உயிரை', 'சேமிப்பு', 'நீங்கள்', 'ஃபக்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'இதுஜாக்', 'லாஸ்லோ', 'லாஸ்லோ', 'லாஸ்லோ', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'ச

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'சந்தோஷ்ம்', 'சுட்டுட்டாங்க', 'பேராசிரியர்', 'பேராசிரியர்', 'பேராசிரியர்', 'பொருத்தப்பட்டிருந்தன', 'விஷயத்தில்', 'செய்தால்', 'செய்தால்', 'செய்தால்', 'வரை', 'வரை', 'விட்டு', 'சாரி', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['கூட', 'இல்லை', 'அவர்', 'உங்களை', 'போன்ற', 'ஒரு', 'அத்தை', 'தான்', 'தேவை', 'இல்லை', 'என்றார்']]
Predicted: ['நம்முடையது', 'நம்முடையது', 'நம்முடையது', 'நம்முடையது', 'நம்முடையது', 'எப்போதும்', 'எப்போதும்', 'எப்போதும்']
Target: [['என்னுடைய', 'மகிழ்ச்சி', 'என்னுடையது', 'என்று', 'நான்', 'சொல்ல', 'விரும்புகிறேன்', 'ஆனால்', 'அது', 'உனக்கும்', 'எனக்கும்', 'அது', 'முக்கியமாக', 'உனக்கு']]
Predicted: ['உங்களுக்குதெரியுமா', 'அவர்கள்சரியானஇங்கேவெறும்', 'தெளிவுபடுத்துக', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'ஷீலா', 'தொடுவாங்க', 'ஏற்படுத்திக்கொண்ட', 'பம்ப்', 'பம்ப்', 'பம்ப்', 'எடுத்தார்', 'உணர்வீர்கள்', 'உணர்வீர்கள்', 'மற்றும்', 'நீங்கள்', 'இல்லை'

(0.006922011998154133,
 1.2410474586157381e-155,
 1.5076726972826827e-206,
 5.254923650570871e-232)

In [57]:
# To obtain bleu scores for the training data
train, _ = train_test_loader(X_train, Y_train, X_test, Y_test, batch_size=1)

In [58]:
test_model(train, trans_model)

Predicted: ['கார்டியன்', 'கார்டியன்', 'கார்டியன்', 'கார்டியன்', 'கார்டியன்', 'கார்டியன்', 'hanginநான்ஏனெனில்', 'தாக்கல்செய்யயாரும்இல்லைஇப்போதுஎதிராக', 'தாக்குதல்கள்', 'தாக்குதல்கள்', 'தாக்குதல்கள்', 'தொடுவாங்க', 'முடியும்', 'முடியும்', 'முடியும்', 'முடியும்', 'செய்யலாம்', 'ஏற்றுக்', 'ஏற்றுக்', 'சாரி', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['துரதிருஷ்டவசமான', 'மக்கள்', 'நிறைய', 'என்ற', 'முதலீடுகள்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'வேண்டிக்கொள்', 'பொறுத்தவேண்டும்', 'பொறுத்தவேண்டும்', 'நினைக்கிறார்கள்']
Target: [['அடடா', 'எனக்கு', 'நேரடியாக', 'ஆனால்', 'ஆமாம்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'angel', 'angel', 'angel', 'angel', 'miller', 'miller', 'வேலைபார்த்தான்', 'பார்க்கும்போது', 'பார்க்கும்போது', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'நேரத்தில்', 'பிடித்த', 'நாடக', 'உன்னோடு', 'உன்னோடு', 'முடியாது']
Target: [['சில', 'நிதிக்காக', 'நிலத்த', 'வித்துட்டோம்']]
Predicted: ['கொடுக்கிறது', 'கொடுக்கிறது

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'விருந்தினர்கள்', 'செய்பவர்கள்', 'செய்பவர்கள்', 'செய்பவர்கள்', 'லதா', 'லதா', 'லதா', 'லதா', 'லதா', 'லதா', 'இதர', 'மற்றும்', 'முடியுமா', 'முடியுமா', 'முடியாது', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['அதை', 'நேருக்கு', 'நேர்']]
Predicted: ['குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைக்கு', 'காத்திருக்கு', 'நிரந்தரமில்லை', 'நிரந்தரமில்லை', 'மேற்கூரைகள்', 'பனிப்பாறைசிக்கி', 'பனிப்பாறைசிக்கி', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'நேரத்தில்', 'நேரத்தில்', 'காவலில்', 'காவலில்', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['இந்தநம்மத்தியில்', 'நடைபயிற்சி', 'குற்றவாளிகள்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', "அவர்களுடன்'", 'மற்றவர்கள்', 'மற்றவர்கள்', 'மற்றவர்கள்']
Target: [['தயவு', 'செய்து']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்தும

Predicted: ['மோதல்', 'மோதல்', 'மோதல்', 'மோதல்', 'மோதல்', 'சூதாட்டம்', 'சூதாட்டம்', 'சூதாட்டம்', 'வியாபாரம்', 'வியாபாரம்', 'அனுப்புகிறார்', 'அனுப்புகிறார்', 'சேமிக்கலாம்', 'பார்க்கலாம்', 'பார்க்கலாம்', 'இங்கே', 'இங்கே', 'குறைந்தபட்சம்', 'ஏனெனில்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நீங்கள்பாதுகாப்புஅதன்', 'என்று', 'பந்தயம்', 'கட்ட', 'முடியும்', 'அதிக']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'negrescu', 'வகையெல்லாம்', 'வகையெல்லாம்', 'பாத்துச்சு', 'பாத்துச்சு', 'பாத்துச்சு', 'தெளிவு', 'தெளிவு', 'தெளிவு', 'தெளிவு', 'படங்கள்', 'படங்கள்', 'படங்கள்', 'காவலில்', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['பொறுத்திவிட்டோம்']]
Predicted: ['கொடுக்கனுமா', 'கொடுக்கனுமா', 'கொடுக்கனுமா', 'தரட்டுமா', 'தரட்டுமா', 'பொறுத்தவேண்டும்', 'பொறுத்தவேண்டும்', 'பொறுத்தவேண்டும்', 'பொறுத்தவேண்டும்', 'நெருங்கியிருப்பர்']
Target: [['பான்சி', 'ஒரு', 'ஐபால்', 'எல்ப்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்',

Predicted: ['கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'கிராஸ்', 'பிளேட்', 'பிளேட்', 'டயர்கள்', 'டயர்கள்', 'டயர்கள்', 'படங்கள்', 'படங்கள்', 'படங்கள்', 'படங்கள்', 'உணர்வீர்கள்', 'உணர்வீர்கள்', 'வேண்டாம்', 'இல்லை', 'இல்லை']
Target: [['அவர்', 'ஒரு', 'சிறிய', 'வரை', 'போலீஸ்', 'தாக்குதல்', 'கிடைத்தது']]
Predicted: ['கிருஸ்துமஸ்', 'கிருஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'வெர்மீர்', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'பைத்தியம்', 'பாம்பு', 'பாம்பு', 'படங்கள்', 'அவர்கள்', 'காவலில்', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நான்', 'கமாண்டர்', 'இன்', 'தலைமை', 'இருக்கிறேன்']]
Predicted: ['பீஸ்ட்', 'பீஸ்ட்', 'பீஸ்ட்', 'பீஸ்ட்', 'பீஸ்ட்', 'பீஸ்ட்', 'கிராஸ்', 'கிராஸ்', 'பிரிஸ்டல்', 'பிரிஸ்டல்', 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'சிக்கலாக', 'சிக்கலாக', 'சிக்கலாக', 'படங்கள்', 'படங்கள்', 'விவகாரங்களை', 'இயங்கும்', 'முடியாது', 'அல்ல', 'இல்லை', 'இல்லை', 

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'பிரார்த்தனைக்குப்', 'திரும்பப்பெறமுடியாத', 'திரும்பப்பெறமுடியாத', 'திரும்பப்பெறமுடியாத', 'திரும்பப்பெறமுடியாத', 'பரிசீலிக்க']
Target: [['அதனால்', 'ஏமாற்றம்', 'இல்லை']]
Predicted: ['ஓப்ரா', 'ஓப்ரா', 'ஓப்ரா', 'ஓப்ரா', 'கான்ட்ரா', 'கான்ட்ரா', 'கான்ட்ரா']
Target: [['நாம்', 'போகி', 'கீழே', 'என்று', 'உறுதி', 'இல்லை', 'ஐயா']]
Predicted: ['குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைக்கு', 'எண்ணத்தில்', 'எண்ணத்தில்', 'எண்ணத்தில்']
Target: [['நாம்', 'முடிந்தால்', 'போல்', 'கிளிக்', 'அது', 'மற்றும்', 'நிறுத்தப்படலாம்', 'மற்றும்', 'சொல்ல']]
Predicted: ['மோதல்', 'மோதல்', 'மோதல்', 'மோதல்', 'மோதல்', 'மோதல்', 'மற்றும்', 'மற்றும்']
Target: [['உங்கள்', 'பிரச்சினையை', 'மனிதன்', 'என்ன']]
Predicted: ['செய்தியை', 'செய்தியை', 'செய்தியை', 'செய்தியை', 'செய்தியை', 'செய்தியை', 'செய்தியை', 'சென்றது', 'சென்றது', 'சென்றது', 'செய்தது', 'செய்தது', 'செய்தது', 'தப்பு', 'தப்பு', 'தப்பு', 'செய்யலாம்', 'டஜன்', 'டஜன்', 'உன்னோடு', 'இல்லை', 'இல்லை', 

...

Predicted: ['குழந்தைக்கு', 'குழந்தைக்கு', 'அனுப்பவும்', 'அனுப்பவும்', 'சரிபார்க்கவும்', 'சரிபார்க்கவும்', 'சரிபார்க்கவும்', 'முயற்சிக்கிறீர்கள்', 'பயன்படுத்துகிறது', 'பயன்படுத்துகிறது', 'போட்டீர்கள்', 'போட்டீர்கள்', 'போட்டீர்கள்', 'முடிந்தது', 'முடிந்தது', 'முடிந்தது', 'மற்றும்', 'மற்றும்', 'மற்றும்', 'காவலில்', 'காவலில்', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['பிளின்ட்']]
Predicted: ['அக்லி', 'அக்லி', 'அக்லி', 'அக்லி', 'அக்லி', 'பெற்டுள்ளனரா', 'பயன்படுத்தும்', 'நிலைதடுமாறி', 'நிலைதடுமாறி', 'பெரிதும்', 'பெரிதும்', 'பெரிதும்', 'முடிந்தது', 'முடிந்தது', 'முடிந்தது', 'முடியுமா', 'முடியுமா', 'காவலில்', 'காவலில்', 'முடியாது', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'எந்த']
Target: [['இறைவா']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்']
Target: [['போன்', 'இல்லை']]
Predicted: ['இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'இரகசிய', 'கிரகமாக', 'அஸ்தமனம்', 'அஸ்தமனம்', 'அஸ்

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'அவர்கள்அழைக்கஒருமனிதன்தியாப்ளோ', 'பேராசிரியர்', 'பேராசிரியர்', 'நான்இங்கேஉட்கார்ந்துமுடியவில்லை', "என்னநரகத்தில்நான்ஓ'கீஃப்சொல்லவேண்டும்", 'பதிக்கப்பட்ட', 'பதிக்கப்பட்ட', 'மற்றும்', 'மற்றும்', 'இதர', 'இதர', 'இதர', 'இதர', 'உன்னோடு', 'அது', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['நான்', 'கதவு', 'வழியாக', 'ஏதாவது', 'put', 'போகிறேன்']]
Predicted: ['குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைகளுக்கு', 'குழந்தைகளுக்கு', 'திரும்பப்பெறமுடியாத', 'ஒப்புக்', 'ஒப்புக்', 'ஒப்புக்']
Target: [['நான்', 'குறைத்து', 'மதிப்பிடப்பட்டுள்ளன']]
Predicted: ['அக்லி', 'அக்லி', 'அக்லி', 'அக்லி', 'நக்கலடிக்கிறாள்', 'நக்கலடிக்கிறாள்', 'வகையெல்லாம்', 'வகையெல்லாம்']
Target: [['இன்னொருநாள்', 'கூப்பிடுறேன்']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'அவர்கள்அழைக்கஒருமனிதன்தியாப்ளோ', 'ஒருமுறைஉங்கள்வாழ்க்கையில்வாழ', 'ஒருமுறைஉங்கள்வாழ்க்கையில்வாழ', 'எனவேஅனைத்துஉங்கள்துணிகளைஎடுத

Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'angel', 'angel', 'angel']
Target: [['நாங்கள்', 'அதை', 'சரியான', 'வடிவமாக', 'மாற்றியுள்ளோம்']]
Predicted: ['காப்பாற்றுங்கள்', 'நிறுத்துங்கள்', 'நிறுத்துங்கள்', 'நிறுத்துங்கள்', 'நிறுத்துங்கள்', 'நிறுத்துங்கள்', 'டயர்கள்', 'டயர்கள்', 'டயர்கள்', 'டயர்கள்', 'டயர்கள்', 'டயர்கள்', 'அனைவரும்எப்போதும்', 'frump', 'பிறகுஒருchickie', 'எல்லாத்தையும்', 'சூழ்நிலையை', 'மற்றும்', 'மற்றும்', 'மற்றும்', 'நீங்கள்', 'இல்லை', 'இல்லை']
Target: [['அப்பா', 'பாருங்கள்']]
Predicted: ['குழந்தைக்கு', 'குழந்தைக்கு', 'குழந்தைகளுக்கு', 'குழந்தைகளுக்கு', 'பயமுறுத்தினா்', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'பிரச்சினைகளை', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'அங்கு', 'அங்கு', 'உன்னோடு', 'உன்னோடு', 'இல்லை', 'இல்லை', 'இல்லை', 'இல்லை']
Target: [['இது', 'தானா']]
Predicted: ['கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'கிறிஸ்துமஸ்', 'நான்உங்கள்சங்கிலிyan

Predicted: ['கொடுக்கனுமா', 'கொடுக்கனுமா', 'கொடுக்கனுமா', 'தரட்டுமா', 'தரட்டுமா', 'நான்சரியாகநினைவில்இல்லை', 'எனவேஅனைத்துஉங்கள்துணிகளைஎடுத்து', 'குழந்தைகளுடன்', 'குழந்தைகளுடன்', 'மார்டின்', 'மார்டின்', 'மார்டின்']
Target: [['நாங்கள்', 'வீட்டை', 'விற்க', 'போகிறேன்', 'என்று']]
Predicted: ['சக்திமிக்கது', 'சக்திமிக்கது', 'செய்யப்படுகிறது', 'செய்யப்படுகிறது', 'விஷயத்தில்', 'விஷயத்தில்', 'விஷயத்தில்', 'சென்டரில்', 'சென்டரில்', 'சென்டரில்', 'தொடங்கிய', 'தொடங்கிய', 'ஆண்டுகளில்', 'ஆண்டுகளில்', 'அப்போதுதான்', 'அப்போதுதான்', 'உணர்வீர்கள்', 'உணர்வீர்கள்', 'காவலில்', 'காவலில்', 'முடியாது', 'இல்லை']
Target: [['வெளிப்படையான', 'கேள்வி']]
Predicted: ['என்சிடபுள்யு', 'லாவன்டர்', 'ட்ரோஜன்', 'ட்ரோஜன்', 'ட்ரோஜன்', 'கான்ட்ரா', 'ரகசியங்களும்']
Target: [['டாக்கெட்ல', 'அப்படித்தான்', 'இருக்கு']]
Predicted: ['யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'யான', 'வலிமை', 'நிச்சயம்', 'சாதாரணமாக', 'எதற்காக', 'எதற்காக', 'எதற்காக', 'காரணமா', 'முடியாது', 'முடியாது', 'இல்லை', 'இல்லை', 'இல்

(0.003576485643698295,
 0.0007719453917180145,
 0.0003284855962345131,
 0.00016046160232477963)